1. What do you think we should do with these null values in the `fresh_segments.interest_metrics`

In [9]:
UPDATE fresh_segments.interest_metrics
SET
    month_year = COALESCE(month_year,'NO RECORD'),
    interest_id = COALESCE(interest_id,'NO RECORD'),
    _month = COALESCE(_month,0),
    _year = COALESCE(_year,0)


(13940 rows affected)

Total execution time: 00:00:00.396

2. What is count of records in the `fresh_segments.interest_metrics` for each `month_year` value sorted in chronological order (earliest to latest) with the null values appearing first?

In [14]:
SELECT 
    CAST(CAST(month_year + '-01' AS nvarchar(10)) AS date) AS ConvertedDate , 
    COUNT(*) AS number_of_records 
FROM fresh_segments.interest_metrics
WHERE month_year != 'NO RECORD'
GROUP BY month_year
ORDER BY month_year


(14 rows affected)

Total execution time: 00:00:00.063

ConvertedDate number_of_records 2018-07-01 729 2018-08-01 767 2018-09-01 780 2018-10-01 857 2018-11-01 928 2018-12-01 995 2019-01-01 973 2019-02-01 1121 2019-03-01 1136 2019-04-01 1099 2019-05-01 524 2019-06-01 824 2019-07-01 864 2019-08-01 1149

3. How many `interest_id` values exist in the `fresh_segments.interest_metrics` table but not in the `fresh_segments.interest_map` table? What about the other way around?

In [10]:
SELECT COUNT(*) as [interest_id values exist]
FROM
    (SELECT 
        DISTINCT(interest_id)
    FROM fresh_segments.interest_metrics
    WHERE interest_id != 'NO RECORD'
    EXCEPT
    SELECT
        DISTINCT(id)
    FROM fresh_segments.interest_map) AS RESULT

---> tìm duy nhất được 1 interest_id

-- what about the other way around?
SELECT COUNT(*) as [interest_id values exist in contrast]
FROM 
    (SELECT
        DISTINCT(id)
    FROM fresh_segments.interest_map
    EXCEPT
    SELECT 
        DISTINCT(interest_id)
    FROM fresh_segments.interest_metrics
    WHERE interest_id != 'NO RECORD') AS RESULT

---> tìm được 7 ids ngược lại

(1 row affected)

(1 row affected)

Total execution time: 00:00:00.143

interest_id values exist 1

interest_id values exist in contrast 7

4. Summarise the `id` values in the `fresh_segments.interest_map` by its total record count in this table

In [11]:
SELECT COUNT(ID) as TOTAL_RECORD
FROM fresh_segments.interest_map;

(1 row affected)

Total execution time: 00:00:00.011

TOTAL_RECORD 1208

5. What sort of table join should we perform for our analysis and why? Check your logic by checking the rows where `interest_id = 21246` in your joined output and include all columns from `fresh_segments.interest_metrics` and all columns from `fresh_segments.interest_map` except from the `id` column.

In [17]:

SELECT
     CAST(CAST(A.month_year + '-01' AS nvarchar(10)) AS date) AS ConvertedDate , A.interest_id , B.interest_name , A.composition , A.index_value , A.ranking , A.percentile_ranking,
        B.interest_summary , B.created_at , B.last_modified
FROM fresh_segments.interest_metrics A JOIN fresh_segments.interest_map B
    ON A.interest_id = B.id
WHERE A.month_year != 'NO RECORD' OR A._month != 0 OR A._year != 0



--- nên sort thứ tự theo 2 trường interest_name (hoặc interest_id) và month_year (cũ nhất - mới nhất).
---- Theo interest_name (hoặc interest_id) chúng ta cần nhóm interest_name lại với nhau để dễ dàng quan sát những kết quả về metric của online ad mà khách hàng đạt được
--- (về thời gian tương tác, khoảng thời gian từ lúc xây dựng 1 online ad cho đến khi đạt được những kết quả metric đầu tiên,... ).
---- Kế tiếp là sort theo month_year là vì chúng ta có thể quan sát trung bình 1 online ad sẽ nhận được sự tương tác của khách hàng trong bao lâu, theo thứ tự earliest - latest
--- là vì chúng ta sẽ quan sát được xu hướng tăng trưởng hay giảm sút trong kết quả các chỉ số

(12745 rows affected)

Displaying Top 5000 rows.

Total execution time: 00:00:00.163

ConvertedDate interest_id interest_name composition index_value ranking percentile_ranking interest_summary created_at last_modified 2018-07-01 32486 Vacation Rental Accommodation Researchers 11.89 6.19 1 99.86 People researching and booking rentals accommodations for vacations. 2018-06-29 12:55:03.000 2018-06-29 12:55:03.000 2018-07-01 6106 Luxury Second Home Owners 9.93 5.31 2 99.73 High income individuals with more than one home. 2017-03-27 16:59:29.000 2018-05-23 11:30:12.000 2018-07-01 18923 Online Home Decor Shoppers 10.85 5.29 3 99.59 Consumers shopping online for home decor available for delivery. 2018-04-19 18:25:02.000 2018-04-19 18:25:02.000 2018-07-01 6344 Hair Care Shoppers 10.32 5.1 4 99.45 Consumers researching trends and purchasing hair and beauty products. 2017-05-15 13:04:55.000 2018-05-31 22:11:37.000 2018-07-01 100 Nutrition Conscious Eaters 10.77 5.04 5 99.31 Consumer reading about healthy eating options. 2016-05-26 14:57:59.000 2018-05-23 11:30:13.000 2018-07-01 69 Healthy Eaters 10.82 5.03 6 99.18 People researching healthy eating options. 2016-05-26 14:57:59.000 2018-05-23 11:30:12.000 2018-07-01 79 Luxury Travel Researchers 11.21 4.97 7 99.04 Consumers reading online reviews of luxury travel options. 2016-05-26 14:57:59.000 2018-05-23 11:30:12.000 2018-07-01 6111 Wine Lovers 10.71 4.83 8 98.9 Consumers researching wine and purchasing alcohol online. These consumers are more likely to purchase wine and visit vineyards. 2017-03-27 16:59:29.000 2017-12-07 12:35:47.000 2018-07-01 6214 Home Remodelers 9.71 4.83 8 98.9 People researching techniques and resources for home remodels. 2017-03-27 16:59:29.000 2018-05-23 11:30:12.000 2018-07-01 19422 Home Design and Living Publication Readers 10.11 4.81 10 98.63 People reading publications focused on design and living at home. 2018-05-08 11:55:03.000 2018-05-08 11:55:03.000 2018-07-01 6110 Apartment Furniture Shoppers 11.57 4.79 11 98.49 Consumers in-market for apartment furniture. 2017-03-27 16:59:29.000 2018-05-23 11:30:12.000 2018-07-01 4895 Mature Parents 9.47 4.67 12 98.35 Parents who had children later in life. 2016-08-11 12:12:27.000 2018-05-23 11:30:12.000 2018-07-01 6217 Weight Loss Researchers 10.8 4.62 13 98.22 Consumers researching weight loss methods. 2017-03-27 16:59:29.000 2018-05-23 11:30:13.000 2018-07-01 4 Luxury Retail Researchers 13.97 4.53 14 98.08 Consumers researching luxury product reviews and gift ideas. 2016-05-26 14:57:59.000 2018-05-23 11:30:12.000 2018-07-01 6218 Running Enthusiasts 9.29 4.5 15 97.94 Consumers who read online publications about running. 2017-03-27 16:59:29.000 2019-01-16 09:11:30.000 2018-07-01 6123 Misc-Deal Seekers or Coupon Shoppers 9.49 4.49 16 97.81 Consumers researching deals and shopping with coupons. 2017-03-27 16:59:29.000 2018-05-23 11:30:13.000 2018-07-01 171 Shoe Shoppers 14.91 4.47 17 97.67 Consumers shopping for mass market shoes. 2016-05-26 14:57:59.000 2018-05-23 11:30:13.000 2018-07-01 19613 Land Rover Shoppers 12.62 4.38 18 97.53 People researching and comparing Land Rover vehicles. These consumers are more likely to spend money on a new or used car. 2018-05-15 14:20:05.000 2018-05-15 14:20:05.000 2018-07-01 17 MLB Fans 7.89 4.15 19 97.39 People reading articles and websites about baseball and the MLB. 2016-05-26 14:57:59.000 2018-05-23 11:30:13.000 2018-07-01 6 Vacation Planners 11.99 4.08 20 97.26 Consumers reading reviews of vacation destinations and accommodations. 2016-05-26 14:57:59.000 2018-05-23 11:30:13.000 2018-07-01 6013 Competitive Sports Participants 9.35 3.99 21 97.12 People registering for competitive sports leagues, races, and events for adults. 2017-03-27 16:36:07.000 2019-01-16 09:11:30.000 2018-07-01 4870 Tech-Savvy Moms 10.29 3.95 22 96.98 People reading tech sites geared to mothers. 2016-06-09 16:28:11.000 2018-05-23 11:30:13.000 2018-07-01 19423 Kitchen Appliance Shoppers 12.22 3.92 23 96.84 People shopping for kitchen appliances. 2018-05-08 11:55:03.000 2018-05-08 11:55:03.000 2

Interest Analysis

1. Which interests have been present in all `month_year` dates in our dataset?

In [18]:
SELECT 
    interest_id,
    COUNT(month_year) AS TOTAL_MONTH
FROM fresh_segments.interest_metrics
GROUP BY interest_id
HAVING COUNT(month_year) = (
    SELECT COUNT(DISTINCT(month_year))
    FROM fresh_segments.interest_metrics
    WHERE month_year != 'no record'
)
-- TOTAL_MONTH: khoảng thời gian dài nhất được ghi nhận mà 1 online ad nhận được sự tương tác từ khách hàng

(327 rows affected)

Total execution time: 00:00:00.090

interest_id TOTAL_MONTH 10008 14 12031 14 5936 14 6314 14 6081 14 6319 14 6304 14 10977 14 10837 14 85 14 5916 14 23778 14 20754 14 6110 14 6393 14 163 14 5913 14 14901 14 17785 14 39 14 4858 14 6386 14 5933 14 17320 14 4912 14 73 14 7527 14 6215 14 10326 14 17314 14 4870 14 6128 14 157 14 18782 14 124 14 6107 14 145 14 4943 14 137 14 158 14 5963 14 17318 14 19338 14 7425 14 108 14 22411 14 4897 14 6284 14 6142 14 18204 14 6088 14 34 14 19630 14 64 14 19519 14 6301 14 6085 14 7535 14 17729 14 6029 14 18997 14 20767 14 95 14 4916 14 6328 14 22502 14 15 14 19600 14 129 14 22421 14 6255 14 19298 14 45 14 143 14 19621 14 22423 14 70 14 6308 14 162 14 6250 14 6340 14 99 14 89 14 10980 14 10832 14 17786 14 19590 14 19619 14 56 14 7546 14 6220 14 6277 14 17674 14 16138 14 6051 14 17673 14 6324 14 17672 14 4902 14 6108 14 49 14 11975 14 10981 14 5968 14 16 14 74 14 16119 14 5921 14 10979 14 14895 14 19250 14 130 14 6315 14 19618 14 7557 14 18995 14 5918 14 19757 14 6095 14 5938 14 17269 14 6 14 22427 14 6305 14 6285 14 7685 14 10250 14 4 14 12025 14 5906 14 77 14 35 14 6264 14 10835 14 7536 14 6286 14 141 14 111 14 17669 14 6323 14 6206 14 19295 14 33191 14 32705 14 6184 14 6389 14 6216 14 6013 14 6030 14 115 14 6144 14 22092 14 20751 14 5901 14 5991 14 31 14 147 14 19625 14 19294 14 88 14 6335 14 7542 14 6112 14 83 14 5960 14 6234 14 75 14 4903 14 5956 14 6218 14 20766 14 17540 14 6208 14 5970 14 21293 14 18350 14 4944 14 113 14 6320 14 12821 14 44 14 7534 14 18622 14 6210 14 17 14 12490 14 16137 14 100 14 5910 14 10974 14 22428 14 19613 14 6077 14 4914 14 6325 14 151 14 82 14 61 14 6159 14 19593 14 86 14 40 14 27 14 32704 14 6390 14 43 14 19578 14 12026 14 4924 14 19592 14 16196 14 20755 14 38 14 6171 14 7529 14 6168 14 10836 14 6143 14 10972 14 96 14 6343 14 19628 14 50 14 4940 14 19617 14 101 14 5969 14 19423 14 6148 14 22093 14 5911 14 6317 14 5896 14 22096 14 107 14 6217 14 18202 14 6232 14 6133 14 10973 14 10988 14 5917 14 7537 14 37 14 10351 14 6062 14 7541 14 32703 14 25 14 12133 14 4909 14 55 14 153 14 5907 14 117 14 6235 14 10284 14 21242 14 126 14 155 14 6023 14 134 14 161 14 18621 14 4911 14 6098 14 6219 14 5944 14 21239 14 6378 14 119 14 102 14 132 14 7540 14 19610 14 6329 14 32486 14 21237 14 6064 14 80 14 21238 14 5958 14 6367 14 5895 14 19603 14 17730 14 18996 14 30 14 13497 14 11974 14 6391 14 60 14 6336 14 33 14 10976 14 6173 14 4908 14 18490 14 18924 14 5967 14 6177 14 6263 14 6207 14 18352 14 6321 14 87 14 18923 14 12027 14 6067 14 11067 14 135 14 4910 14 18998 14 19624 14 10953 14 10249 14 98 14 21292 14 5898 14 6045 14 160 14 18347 14 79 14 22403 14 18 14 171 14 22417 14

2. Using this same `total_months` measure - calculate the cumulative percentage of all records starting at 14 months - which `total_months` value passes the 90% cumulative percentage value?

In [19]:
DECLARE @total FLOAT
SELECT 
     @total = SUM(TOTAL_MONTH) 
FROM (
    SELECT 
        interest_id,
        COUNT(month_year) AS TOTAL_MONTH
    FROM fresh_segments.interest_metrics
    WHERE month_year != 'no record'
    GROUP BY interest_id
) AS result;

WITH CTE AS 
    (SELECT 
        interest_id,
        TOTAL_MONTH,
        -- Tính tổng tích lũy (Cumulative Sum) từ dòng hiện tại đến tất cả các dòng trước đó
        SUM(TOTAL_MONTH) OVER (ORDER BY TOTAL_MONTH DESC ROWS BETWEEN UNBOUNDED PRECEDING AND CURRENT ROW) AS cumulative_sum
    FROM (
        SELECT 
            interest_id,
            COUNT(month_year) AS TOTAL_MONTH
        FROM fresh_segments.interest_metrics
        WHERE month_year != 'no record'
        GROUP BY interest_id
    ) AS RESULT2)
, CTE1 AS
	(SELECT 
		interest_id,
		TOTAL_MONTH,
		cumulative_sum,
		ROUND(cast( (cumulative_sum / @total) as float)*100,2) AS cumulative_percentage
	FROM CTE) 

SELECT 
	interest_id,
	TOTAL_MONTH,
	cumulative_percentage
FROM CTE1
WHERE cumulative_percentage > 90

-- Trong tập dữ liệu, thời dài nhất mà một online ad nhận được sự tương tác từ khách hàng là 14 tháng.
-- Trong đó, chiếm 10% là các online ad có thời gian tương tác với khách hàng ít hơn 8 tháng

(246 rows affected)

Total execution time: 00:00:00.186

interest_id TOTAL_MONTH cumulative_percentage 57 8 90.06 6363 8 90.12 5900 7 90.18 4847 7 90.23 45725 7 90.29 45673 7 90.34 45674 7 90.4 45675 7 90.45 45676 7 90.51 45677 7 90.56 45678 7 90.62 45521 7 90.67 45667 7 90.73 45670 7 90.78 45671 7 90.84 44587 7 90.89 44588 7 90.95 44589 7 91 45516 7 91.06 45518 7 91.11 45519 7 91.17 44581 7 91.22 44585 7 91.28 44479 7 91.33 44480 7 91.39 44481 7 91.44 44465 7 91.5 44476 7 91.55 44477 7 91.61 44489 7 91.66 44490 7 91.72 40686 7 91.77 41061 7 91.82 41066 7 91.88 41853 7 91.93 41857 7 91.99 43546 7 92.04 44381 7 92.1 44272 7 92.15 44378 7 92.21 43540 7 92.26 42368 7 92.32 42011 7 92.37 44389 7 92.43 44445 7 92.48 44446 7 92.54 44447 7 92.59 44448 7 92.65 44450 7 92.7 44455 7 92.76 44456 7 92.81 44453 7 92.87 44468 7 92.92 44469 7 92.98 44470 7 93.03 44472 7 93.09 44473 7 93.14 34636 7 93.2 34649 7 93.25 33970 7 93.31 22406 7 93.36 22408 7 93.42 39645 7 93.47 39338 7 93.53 39547 7 93.58 39199 7 93.64 39192 7 93.69 39189 7 93.75 39190 7 93.8 39194 7 93.86 39333 7 93.91 39651 7 93.97 39770 7 94.02 39767 7 94.08 39659 7 94.13 40188 7 94.19 40193 7 94.24 37408 7 94.3 36881 7 94.35 37412 7 94.41 20752 7 94.46 19599 7 94.52 15877 7 94.57 10955 6 94.62 10839 6 94.66 19635 6 94.71 19616 6 94.76 37421 6 94.81 39191 6 94.85 20764 6 94.9 23 6 94.95 34641 6 94.99 33958 6 95.04 44474 6 95.09 44457 6 95.14 44458 6 95.18 44452 6 95.23 44449 6 95.28 44391 6 95.32 44444 6 95.37 44383 6 95.42 44386 6 95.47 44387 6 95.51 42000 6 95.56 42479 6 95.61 44379 6 95.65 43547 6 95.7 43545 6 95.75 41551 6 95.79 41065 6 95.84 41062 6 95.89 41048 6 95.94 40702 6 95.98 40695 6 96.03 40427 6 96.08 44478 6 96.12 44466 6 96.17 44586 6 96.22 44582 6 96.27 44487 6 96.31 44488 6 96.36 44584 6 96.41 45526 6 96.45 45662 6 96.5 45664 6 96.55 45679 6 96.6 46134 6 96.64 47850 6 96.69 6131 6 96.74 6298 6 96.78 48154 5 96.82 48462 5 96.86 49979 5 96.9 46132 5 96.94 47130 5 96.98 47713 5 97.02 45524 5 97.06 45669 5 97.1 45672 5 97.14 44579 5 97.18 45520 5 97.21 45517 5 97.25 45515 5 97.29 44467 5 97.33 44491 5 97.37 40687 5 97.41 40689 5 97.45 41546 5 97.49 41194 5 97.53 43549 5 97.57 44385 5 97.61 44459 5 97.65 44462 5 97.69 44463 5 97.72 44475 5 97.76 33957 5 97.8 39647 5 97.84 20756 5 97.88 150 5 97.92 16198 5 97.96 131 5 98 44471 4 98.03 44464 4 98.06 44454 4 98.09 44460 4 98.12 44451 4 98.16 44388 4 98.19 44384 4 98.22 44390 4 98.25 43548 4 98.28 43543 4 98.31 44380 4 98.34 44382 4 98.38 43551 4 98.41 43541 4 98.44 40684 4 98.47 44537 4 98.5 44482 4 98.53 44483 4 98.56 44484 4 98.6 44485 4 98.63 44486 4 98.66 44583 4 98.69 45527 4 98.72 45528 4 98.75 45668 4 98.78 45525 4 98.82 45522 4 98.85 45665 4 98.88 45666 4 98.91 46566 4 98.94 45685 4 98.97 50860 4 99 49973 4 99.03 49974 4 99.07 49976 4 99.1 49502 4 99.13 48463 4 99.16 48465 4 99.19 48460 4 99.22 51120 4 99.25 6010 4 99.29 5984 3 99.31 51678 3 99.33 51119 3 99.36 49977 3 99.38 49978 3 99.4 47065 3 99.43 47115 3 99.45 45523 3 99.47 44580 3 99.5 40694 3 99.52 42399 3 99.54 136 3 99.57 15882 3 99.59 10366 3 99.62 18348 3 99.64 33533 3 99.66 34645 2 99.68 34951 2 99.69 39655 2 99.71 17274 2 99.73 14802 2 99.74 133 2 99.76 42012 2 99.77 43552 2 99.79 46567 2 99.8 49975 2 99.82 49972 2 99.84 48459 2 99.85 48022 2 99.87 6236 2 99.88 6260 2 99.9 5999 1 99.91 42008 1 99.91 42401 1 99.92 44461 1 99.93 40701 1 99.94 15883 1 99.95 106 1 99.95 10365 1 99.96 10011 1 99.97 10954 1 99.98 19626 1 99.98 34950 1 99.99 33534 1 100

3. If we were to remove all `interest_id` values which are lower than the `total_months` value we found in the previous question - how many total data points would we be removing?

In [20]:
SELECT 
    COUNT(T1.interest_id) AS [NUMBER OF RECORDS REMOVED]
FROM fresh_segments.interest_metrics T1 JOIN (
    SELECT 
        interest_id,
        COUNT(month_year) AS 'TOTAL MONTH'
    FROM fresh_segments.interest_metrics
    GROUP BY INTEREST_ID
    HAVING COUNT(month_year) <= 8    
) T2
    ON T1.interest_id = T2.interest_id


(1 row affected)

Total execution time: 00:00:00.049

NUMBER OF RECORDS REMOVED 1827

4. Does this decision make sense to remove these data points from a business perspective? Use an example where there are all 14 months present to a removed `interest` example for your arguments - think about what it means to have less months present from a segment perspective.

Từ khía cạnh doanh nghiệp:

- 1 strategic online ad có thể nằm trong 1 chiến lược hoạt động của business customer hoặc cùng 1 segment marketing online, giả sử một sản phẩm mới được tung ra và sản phẩm online ad được dùng để quan sát cảm nhận người tiêu dùng đối với sản phẩm trong thời gian ngắn, việc remove những records này đồng nghĩa với việc Fresh_Segments đưa ra nhìn nhận chủ quan khi cho rằng những online ad này không hiệu quả vì thời gian tương tác với khách hàng quá ít hoặc số lượng online ad nằm trong 1 phân khúc cụ thể không quá nhiều.

Từ khía cạnh người phân tích dữ liệu:

- Cần tìm hiểu xem những ad online này có cùng thuộc 1 business customer, chiến lược phía sau cũng như mục đích của business customer khi launch những strategic online ad này là gì,..

- Những metrics của các online ad này có phải outliers value trong dataset hay không? (Bởi vì outliers có thể ảnh hưởng cả tích cực lẫn tiêu cực đến quá trình phân tích)

--> Việc đưa ra quyết định loại bỏ ngay những records có thời gian tương tác với khách hàng ít hơn 8 tháng là không hợp lý.

5. After removing these interests - how many unique interests are there for each month?

In [18]:
WITH CTE1 AS 
(    SELECT 
        interest_id,
        COUNT(month_year) AS TOTAL_MONTH
    FROM fresh_segments.interest_metrics
    WHERE month_year != 'NO RECORD'
    GROUP BY interest_id
    HAVING COUNT(month_year) <= 8)
, CTE2 AS 
(    SELECT 
        CAST(CAST(month_year + '-01' AS nvarchar(10)) AS date) AS ConvertedDate,
        interest_id
    FROM fresh_segments.interest_metrics
    WHERE interest_id NOT IN (
        SELECT 
            interest_id
        FROM CTE1
    ) AND month_year != 'NO RECORD')

SELECT 
    ConvertedDate,
    COUNT(DISTINCT(interest_id)) AS [NUMBER OF UNIQUE INTEREST]
FROM CTE2
GROUP BY ConvertedDate
ORDER BY ConvertedDate;

(14 rows affected)

Total execution time: 00:00:00.349

ConvertedDate NUMBER OF UNIQUE INTEREST 2018-07-01 681 2018-08-01 720 2018-09-01 744 2018-10-01 792 2018-11-01 848 2018-12-01 884 2019-01-01 861 2019-02-01 885 2019-03-01 885 2019-04-01 861 2019-05-01 458 2019-06-01 700 2019-07-01 728 2019-08-01 872

Segment Analysis

1. Using our filtered dataset by removing the interests with less than 6 months worth of data, which are the top 10 and bottom 10 interests which have the largest composition values in any `month_year`? Only use the maximum composition value for each interest but you must keep the corresponding `month_year`

In [ ]:
CREATE VIEW filtered_data as
    WITH CTE1 AS 
    (    SELECT
            interest_id,
            COUNT(month_year) AS TOTAL_MONTH
        FROM fresh_segments.interest_metrics
        WHERE month_year != 'NO RECORD'
        GROUP BY interest_id
        HAVING COUNT(month_year) > 6)
    , CTE2 AS (
        SELECT 
            _month,
            _year,
            month_year,
            interest_id,
            composition,
            index_value,
            ranking,
            percentile_ranking
        FROM fresh_segments.interest_metrics
        WHERE interest_id IN 
            (
                SELECT interest_id
                FROM CTE1
            ) AND month_year != 'NO RECORD'
    )
    SELECT * FROM CTE2

In [19]:
;WITH CTE0 AS
    (SELECT 
        CAST(CAST(month_year + '-01' AS nvarchar(10)) AS date) AS ConvertedDate,
        interest_id,
        composition,
        DENSE_RANK() OVER (PARTITION BY interest_id ORDER BY composition DESC) AS [COMPOSITION RANK TEMP]
    FROM filtered_data),
CTE1 AS (
    SELECT
        ConvertedDate,
        interest_id,
        composition
    FROM CTE0 
    WHERE [COMPOSITION RANK TEMP] = 1 --- Lấy những composition cao nhất của mỗi interest_id
), --- Lấy top 10
CTE2 AS (
    SELECT TOP 10
        ConvertedDate,
        interest_id,
        composition,
        DENSE_RANK() OVER (ORDER BY composition DESC) AS [COMPOSITION RANK]
    FROM CTE1
), --- lấy bottom 10
CTE3 AS (
    SELECT
        ConvertedDate,
        interest_id,
        composition,
        DENSE_RANK() OVER (ORDER BY composition DESC) AS [COMPOSITION RANK]
    FROM CTE1
    ORDER BY composition DESC
    OFFSET ((SELECT COUNT(interest_id) FROM CTE1) - 10) ROWS
    FETCH NEXT 10 ROWS ONLY
)
--- nối top 10 với bottom 10
SELECT * FROM CTE2
UNION
SELECT * FROM CTE3
ORDER BY [COMPOSITION RANK]

(20 rows affected)

Total execution time: 00:00:00.939

ConvertedDate interest_id composition COMPOSITION RANK 2018-12-01 21057 21.2 1 2018-07-01 6284 18.82 2 2018-07-01 39 17.44 3 2018-07-01 77 17.19 4 2018-10-01 12133 15.15 5 2018-12-01 5969 15.05 6 2018-07-01 171 14.91 7 2018-07-01 4898 14.23 8 2018-07-01 6286 14.1 9 2018-07-01 4 13.97 10 2018-07-01 20752 2.22 540 2019-08-01 19632 2.22 540 2018-07-01 58 2.18 541 2019-02-01 36138 2.18 541 2019-08-01 34085 2.14 542 2018-07-01 22408 2.12 543 2019-01-01 42011 2.09 544 2018-10-01 19591 2.08 545 2019-03-01 19599 1.97 546 2018-10-01 37412 1.94 547

2. Which 5 interests had the lowest average `ranking` value?

In [12]:
WITH CTE0 AS 
    (SELECT 
        interest_id,
        AVG(ranking) AS AVERAGE_VALUE
    FROM filtered_data
    GROUP BY interest_id , ranking)

SELECT TOP 5
    interest_id,
    AVERAGE_VALUE AS LOWEST_AVG_RANKING,
    DENSE_RANK() OVER (ORDER BY AVERAGE_VALUE ASC) AS AVERAGE_RANKING_VALUE
FROM CTE0 

(5 rows affected)

Total execution time: 00:00:07.795

interest_id LOWEST_AVG_RANKING AVERAGE_RANKING_VALUE 6285 1 1 32486 1 1 6218 1 1 41548 1 1 42203 2 2

3. Which 5 interests had the largest standard deviation in their `percentile_ranking` value?

In [15]:
WITH CTE0 AS 
    (SELECT 
        interest_id,
        percentile_ranking,
        ROUND(
            AVG(percentile_ranking) OVER (PARTITION BY interest_id),2) AS AVG_BY_PERCENTILE_RANKING,
        ROUND(
            POWER(
                (percentile_ranking - ROUND(AVG(percentile_ranking) OVER (PARTITION BY interest_id),2)),2),2) AS SQUARE_OF_DIFF
    FROM FILTERED_DATA),
CTE1 AS 
    (SELECT
        interest_id,
        percentile_ranking,
        AVG_BY_PERCENTILE_RANKING,
        SQUARE_OF_DIFF,
        ROUND(
            SQRT(
                SUM(SQUARE_OF_DIFF) OVER (PARTITION BY interest_id) / 
                    COUNT(interest_id) OVER (PARTITION BY interest_id)),2) AS STANDARD_DEVIATION
    FROM CTE0),
CTE2 AS
    (
        SELECT
            DISTINCT(STANDARD_DEVIATION), 
            interest_id
        FROM CTE1
        ORDER BY STANDARD_DEVIATION DESC
        OFFSET 0 ROW
        FETCH NEXT 5 ROWS ONLY
    )

SELECT 
    interest_id,
    STANDARD_DEVIATION
FROM CTE2

(5 rows affected)

Total execution time: 00:00:00.250

interest_id STANDARD_DEVIATION 38992 27.95 43546 26.01 6087 23.68 103 23.45 4855 23.14

4. For the 5 interests found in the previous question - what was minimum and maximum `percentile_ranking` values for each interest and its corresponding `year_month` value? Can you describe what is happening for these 5 interests?

In [23]:
WITH CTE0 AS 
    (SELECT 
        interest_id,
        percentile_ranking,
        ROUND(
            AVG(percentile_ranking) OVER (PARTITION BY interest_id),2) AS AVG_BY_PERCENTILE_RANKING,
        ROUND(
            POWER(
                (percentile_ranking - ROUND(AVG(percentile_ranking) OVER (PARTITION BY interest_id),2)),2),2) AS SQUARE_OF_DIFF
    FROM FILTERED_DATA),
CTE1 AS 
    (SELECT
        interest_id,
        percentile_ranking,
        AVG_BY_PERCENTILE_RANKING,
        SQUARE_OF_DIFF,
        ROUND(
            SQRT(
                SUM(SQUARE_OF_DIFF) OVER (PARTITION BY interest_id) / 
                    COUNT(interest_id) OVER (PARTITION BY interest_id)),2) AS STANDARD_DEVIATION
    FROM CTE0),
CTE2 AS
    (SELECT
        DISTINCT(STANDARD_DEVIATION),
        interest_id
    FROM CTE1
    ORDER BY STANDARD_DEVIATION DESC
    OFFSET 0 ROW
    FETCH NEXT 5 ROWS ONLY),
CTE3 AS (
    SELECT 
        DISTINCT(interest_id),
        MIN(percentile_ranking) OVER (PARTITION BY interest_id ) AS MIN_PERCENTILE_RANKING,
        MAX(percentile_ranking) OVER (PARTITION BY interest_id ) AS MAX_PERCENTILE_RANKING
    FROM filtered_data
    WHERE interest_id IN 
        (
            SELECT 
                interest_id
            FROM CTE2 
        )
),
CTE4 AS --- Lấy những month_year của interest_id percentile_rank thấp nhất
    (
        SELECT 
        T1.interest_id , CAST(CAST(T2.month_year + '-01' AS nvarchar(10)) AS date) AS MONTH_YEAR_MIN_PERCENTILE, T1.MIN_PERCENTILE_RANKING
    FROM CTE3 T1 JOIN filtered_data T2
        ON T1.interest_id = T2.interest_id AND T1.MIN_PERCENTILE_RANKING = T2.percentile_ranking
    ),
CTE5 AS --- Lấy những month_year của interest_id percentile_rank cao nhất
    (
        SELECT 
            T1.interest_id , CAST(CAST(T2.month_year + '-01' AS nvarchar(10)) AS date) AS MONTH_YEAR_MAX_PERCENTILE, T1.MAX_PERCENTILE_RANKING
        FROM CTE3 T1 JOIN filtered_data T2
            ON T1.interest_id = T2.interest_id AND T1.MAX_PERCENTILE_RANKING = T2.percentile_ranking 
    )

SELECT 
    U1.interest_id ,
    U2.MONTH_YEAR_MAX_PERCENTILE,
    U2.MAX_PERCENTILE_RANKING,
    U1.MONTH_YEAR_MIN_PERCENTILE,
    U1.MIN_PERCENTILE_RANKING,
    DATEDIFF(MONTH,U2.MONTH_YEAR_MAX_PERCENTILE,U1.MONTH_YEAR_MIN_PERCENTILE) AS [TIME_INTERVAL(MONTH)]
FROM CTE4 U1 JOIN CTE5 U2 
    ON U1.interest_id = U2.interest_id 

--- càng về sau, tỷ lệ về thứ hạng index_value của các interest này đều giảm mạnh. Trong vòng 1 năm, mức độ tương tác của khách hàng đối với online ad này giảm đáng kể.

(5 rows affected)

Total execution time: 00:02:00.058

interest_id MONTH_YEAR_MAX_PERCENTILE MAX_PERCENTILE_RANKING MONTH_YEAR_MIN_PERCENTILE MIN_PERCENTILE_RANKING TIME_INTERVAL(MONTH) 103 2018-07-01 95.61 2019-07-01 18.75 12 4855 2018-07-01 88.2 2018-11-01 13.15 4 6087 2018-07-01 81.89 2019-02-01 0.71 7 38992 2018-11-01 82.44 2019-07-01 2.2 8 43546 2019-03-01 73.15 2019-06-01 5.7 3

5. How would you describe our customers in this segment based off their composition and ranking values? What sort of products or services should we show to these customers and what should we avoid?

In [13]:
--- average ranking như thế nào? 
--- Engagement time như thế nào?
--- Thời gian từ lúc launch online ad cho đến khi đạt được max Composition là bao lâu?
WITH CTE0 AS 
    (SELECT
        DISTINCT(interest_name) AS INTEREST_NAME,
        (MAX(T1.RANKING) OVER (PARTITION BY CAST(T2.interest_name AS VARCHAR(255))) - MIN(T1.ranking) OVER (PARTITION BY CAST(T2.interest_name AS VARCHAR(255)))) AS RANKING_RANGE
    FROM filtered_data T1 JOIN fresh_segments.interest_map T2 
        ON T1.interest_id = T2.id),
CTE1 AS
    (
    SELECT
        T2.interest_name,
        CAST(CAST(T1.month_year + '-01' AS nvarchar(10)) AS date) AS ConvertedDate
    FROM filtered_data T1 JOIN fresh_segments.interest_map T2
        ON T1.interest_id = T2.id
    ),
CTE2 AS 
    (
        SELECT
            DISTINCT(interest_name),
            DATEDIFF(MONTH,
                MIN(ConvertedDate) OVER (PARTITION BY interest_name ORDER BY ConvertedDate),
                    MAX(ConvertedDate) OVER (PARTITION BY interest_name ORDER BY ConvertedDate)) AS ENGAGEMENT_TIME
        FROM CTE1 
    ),
CTE4 AS 
    (    SELECT 
            DISTINCT(interest_name) AS INTEREST_NAME,
            T2.created_at,
            MAX(T1.composition) OVER (PARTITION BY CAST(T2.interest_name AS VARCHAR(255)) ORDER BY CAST(T2.interest_name AS VARCHAR(255))) MAX_COMPOSITION
        FROM filtered_data T1 JOIN fresh_segments.interest_map T2
            ON T1.interest_id = T2.id),
CTE5 AS
    (SELECT 
        D3.INTEREST_NAME,
        D3.created_at,
        D1._month,
        D1._year,
        D3.MAX_COMPOSITION
    FROM (filtered_data D1 JOIN fresh_segments.interest_map D2 
        ON D1.interest_id = D2.id) JOIN CTE4 D3 
            ON D2.interest_name = D3.INTEREST_NAME AND D3.MAX_COMPOSITION = D1.composition)

SELECT 
    P1.INTEREST_NAME,
    P3.RANKING_RANGE,
    P2.ENGAGEMENT_TIME,
    (CASE 
        WHEN P1._year = YEAR(P1.created_at) THEN P1._month - MONTH(P1.created_at)
            ELSE (12 - MONTH(P1.created_at)) + P1._month END) AS [HIGHEST COMPOSITION TIME(MONTH)]
FROM (CTE5 P1 JOIN CTE2 P2 
    ON P1.INTEREST_NAME = P2.INTEREST_NAME) JOIN CTE0 P3
        ON P1.INTEREST_NAME = P3.INTEREST_NAME
ORDER BY [HIGHEST COMPOSITION TIME(MONTH)] ASC ,
            ENGAGEMENT_TIME DESC ,
                RANKING_RANGE ASC

--- có thể miêu tả khách hàng theo 3 tiêu chí đó chính
-- RANKING RANGE: cho biết phạm vi của ranking của các online ad, nếu có giá trị lớn, các thứ hạng của online ad này phân tán rộng, có sự khác biệ1 nhiều giữa thứ hạng lớn nhất và nhỏ nhất & ngược lại
-- ENGAGEMENT TIME: thời gian tối đa online ad nhận được sự tương tác từ khách hàng
-- HIGHEST COMPOSITION TIME: khoảng thời gian mà online ad đạt được max Composition


--- Dựa trên các chỉ tiêu này, có thể sắp xếp những online ad có Highest Composition Time ngắn nhất, sau đó là đến những online ad có Engagement Time lâu nhất.

(12210 rows affected)

Displaying Top 5000 rows.

Total execution time: 00:00:38.564

INTEREST_NAME RANKING_RANGE ENGAGEMENT_TIME HIGHEST COMPOSITION TIME(MONTH) Major Airline Customers 169 13 0 Romantics 515 13 0 Sun Protection Shoppers 76 12 0 Major Airline Customers 169 12 0 Jazz Festival Enthusiasts 210 12 0 Toronto Blue Jays Fans 311 12 0 Candy Shoppers 356 12 0 Pittsburgh Steelers Fans 467 12 0 Cookie Eaters 491 12 0 New England Patriots Fans 498 12 0 New York Yankees Fans 550 12 0 Romance Movie and TV enthusiasts 589 12 0 Soda Drinkers 670 12 0 Detroit Red Wings Fans 712 12 0 Denver Broncos Fans 784 12 0 Sun Protection Shoppers 76 11 0 Major Airline Customers 169 11 0 Jazz Festival Enthusiasts 210 11 0 Toronto Blue Jays Fans 311 11 0 Candy Shoppers 356 11 0 Pittsburgh Steelers Fans 467 11 0 Cookie Eaters 491 11 0 New England Patriots Fans 498 11 0 New York Yankees Fans 550 11 0 Soda Drinkers 670 11 0 Sun Protection Shoppers 76 10 0 Solitaire Players 118 10 0 Major Airline Customers 169 10 0 Spain Trip Planners 179 10 0 Jazz Festival Enthusiasts 210 10 0 Grateful Dead Fans 296 10 0 Toronto Blue Jays Fans 311 10 0 South Atlantic Voters 328 10 0 Candy Shoppers 356 10 0 Womens Subscription Box Shoppers 362 10 0 Volvo Vehicle Shoppers 464 10 0 Cookie Eaters 491 10 0 New England Patriots Fans 498 10 0 Chess Enthusiasts 515 10 0 Green Party Policy Supporters 530 10 0 New York Yankees Fans 550 10 0 Soda Drinkers 670 10 0 Sun Protection Shoppers 76 9 0 Solitaire Players 118 9 0 Major Airline Customers 169 9 0 Spain Trip Planners 179 9 0 Jazz Festival Enthusiasts 210 9 0 Grateful Dead Fans 296 9 0 Toronto Blue Jays Fans 311 9 0 Rome Trip Planners 318 9 0 South Atlantic Voters 328 9 0 Candy Shoppers 356 9 0 Womens Subscription Box Shoppers 362 9 0 New England Patriots Fans 498 9 0 Chess Enthusiasts 515 9 0 Romantics 515 9 0 Green Party Policy Supporters 530 9 0 New York Yankees Fans 550 9 0 Winter Apparel Shoppers 0 8 0 Fitness Activity Tracker Users 7 8 0 Sun Protection Shoppers 76 8 0 Solitaire Players 118 8 0 Major Airline Customers 169 8 0 Spain Trip Planners 179 8 0 Jazz Festival Enthusiasts 210 8 0 Grateful Dead Fans 296 8 0 Toronto Blue Jays Fans 311 8 0 Rome Trip Planners 318 8 0 South Atlantic Voters 328 8 0 Candy Shoppers 356 8 0 Womens Subscription Box Shoppers 362 8 0 Pittsburgh Steelers Fans 467 8 0 Cookie Eaters 491 8 0 New England Patriots Fans 498 8 0 Chess Enthusiasts 515 8 0 Romantics 515 8 0 Green Party Policy Supporters 530 8 0 New York Yankees Fans 550 8 0 Romance Movie and TV enthusiasts 589 8 0 Soda Drinkers 670 8 0 Denver Broncos Fans 784 8 0 Winter Apparel Shoppers 0 7 0 Fitness Activity Tracker Users 7 7 0 Sun Protection Shoppers 76 7 0 Solitaire Players 118 7 0 Major Airline Customers 169 7 0 Spain Trip Planners 179 7 0 Jazz Festival Enthusiasts 210 7 0 Grateful Dead Fans 296 7 0 Toronto Blue Jays Fans 311 7 0 Rome Trip Planners 318 7 0 Candy Shoppers 356 7 0 Pittsburgh Steelers Fans 467 7 0 Cookie Eaters 491 7 0 New England Patriots Fans 498 7 0 Chess Enthusiasts 515 7 0 Romantics 515 7 0 New York Yankees Fans 550 7 0 Romance Movie and TV enthusiasts 589 7 0 Soda Drinkers 670 7 0 Detroit Red Wings Fans 712 7 0 Denver Broncos Fans 784 7 0 Winter Apparel Shoppers 0 6 0 Fitness Activity Tracker Users 7 6 0 Volleyball Enthusiasts 43 6 0 Sun Protection Shoppers 76 6 0 Solitaire Players 118 6 0 Trampoline Shoppers 119 6 0 Major Airline Customers 169 6 0 Spain Trip Planners 179 6 0 Rock Climbing Enthusiasts 197 6 0 Jazz Festival Enthusiasts 210 6 0 Womens Swimsuit Shoppers 214 6 0 Grateful Dead Fans 296 6 0 Mens Suit Shoppers 306 6 0 Toronto Blue Jays Fans 311 6 0 Rome Trip Planners 318 6 0 South Atlantic Voters 328 6 0 Sleepwear Shoppers 350 6 0 Basketball Enthusiasts 352 6 0 Candy Shoppers 356 6 0 Womens Subscription Box Shoppers 362 6 0 Blades and Hunting Knife Shoppers 364 6 0 Volvo Vehicle Shoppers 464 6 0 Pittsburgh Steelers Fans 467 6 0 Cookie Eaters 491 6 0 New England Patriots Fans 498 6 0 Chess Enthusiasts 515 6 0 Romantics 515 6 0 Green Party Policy Supporters 530 6 0 New York Yankee

Index Analysis
1. What is the top 10 interests by the average composition for each month?

In [25]:
WITH CTE0 AS 
    (SELECT 
        CAST(CAST(month_year + '-01' AS nvarchar(10)) AS date) AS ConvertedDate,
        interest_id,
        AVG(composition) OVER (PARTITION BY month_year , interest_id ORDER BY composition DESC) AS AVG_COMPOSITION
    FROM filtered_data
    ),
CTE1 AS
    (
    SELECT 
        ConvertedDate,
        interest_id,
        AVG_COMPOSITION,
        DENSE_RANK() OVER (PARTITION BY ConvertedDate ORDER BY AVG_COMPOSITION DESC) AS AVG_COMPOSITION_RANKING
    FROM CTE0
    )

SELECT 
    ConvertedDate,
    interest_id,
    AVG_COMPOSITION,
    AVG_COMPOSITION_RANKING
FROM CTE1
WHERE AVG_COMPOSITION_RANKING <= 10


(143 rows affected)

Total execution time: 00:00:00.824

ConvertedDate interest_id AVG_COMPOSITION AVG_COMPOSITION_RANKING 2018-07-01 6284 18.82 1 2018-07-01 39 17.44 2 2018-07-01 77 17.19 3 2018-07-01 171 14.91 4 2018-07-01 4898 14.23 5 2018-07-01 6286 14.1 6 2018-07-01 4 13.97 7 2018-07-01 17786 13.67 8 2018-07-01 6184 13.35 9 2018-07-01 4897 12.93 10 2018-08-01 6284 13.9 1 2018-08-01 77 12.73 2 2018-08-01 21057 12.42 3 2018-08-01 39 12.03 4 2018-08-01 5969 10.85 5 2018-08-01 12133 10.26 6 2018-08-01 6286 9.1 7 2018-08-01 19298 9.06 8 2018-08-01 115 8.98 9 2018-08-01 6206 8.82 10 2018-09-01 21057 18.18 1 2018-09-01 5969 14.29 2 2018-09-01 12133 12.8 3 2018-09-01 64 11.93 4 2018-09-01 19298 11.74 5 2018-09-01 6286 11.18 6 2018-09-01 6284 11.06 7 2018-09-01 10977 10.61 8 2018-09-01 77 10.28 9 2018-09-01 6343 9.96 10 2018-10-01 21057 20.28 1 2018-10-01 12133 15.15 2 2018-10-01 5969 14.15 3 2018-10-01 19298 13.03 4 2018-10-01 6284 12.64 5 2018-10-01 6 12.56 6 2018-10-01 6286 12.47 7 2018-10-01 64 12.33 8 2018-10-01 10977 12.16 9 2018-10-01 158 11.97 10 2018-11-01 21057 19.45 1 2018-11-01 5969 14.92 2 2018-11-01 12133 12.68 3 2018-11-01 19298 11.93 4 2018-11-01 6286 11.14 5 2018-11-01 6284 11.06 6 2018-11-01 10977 10.88 7 2018-11-01 64 10.69 8 2018-11-01 19621 10 9 2018-11-01 10981 9.85 10 2018-12-01 21057 21.2 1 2018-12-01 5969 15.05 2 2018-12-01 12133 13.81 3 2018-12-01 19298 12.62 4 2018-12-01 64 12.41 5 2018-12-01 77 11.74 6 2018-12-01 10977 11.57 7 2018-12-01 6286 11.5 8 2018-12-01 34 11.23 9 2018-12-01 6 11.08 10 2019-01-01 21057 18.99 1 2019-01-01 5969 14.92 2 2019-01-01 12133 12.26 3 2019-01-01 64 11.75 4 2019-01-01 19298 11.71 5 2019-01-01 10977 10.96 6 2019-01-01 77 10.42 7 2019-01-01 6286 10.12 8 2019-01-01 34 10.07 9 2019-01-01 10981 9.91 10 2019-02-01 21057 18.39 1 2019-02-01 5969 14.39 2 2019-02-01 12133 13.64 3 2019-02-01 19298 12.85 4 2019-02-01 6286 12.41 5 2019-02-01 6 11.03 6 2019-02-01 64 10.99 7 2019-02-01 6284 10.61 8 2019-02-01 5960 10.52 9 2019-02-01 10977 10.52 9 2019-02-01 6343 10.38 10 2019-03-01 12133 12.64 1 2019-03-01 5969 12.3 2 2019-03-01 19298 11.27 3 2019-03-01 6286 10.99 4 2019-03-01 6 10.57 5 2019-03-01 10977 10.5 6 2019-03-01 6343 10.48 7 2019-03-01 6284 10.43 8 2019-03-01 7541 9.88 9 2019-03-01 5960 9.82 10 2019-04-01 5969 11.01 1 2019-04-01 12133 10.51 2 2019-04-01 10977 9.95 3 2019-04-01 64 9.7 4 2019-04-01 19298 9.43 5 2019-04-01 6284 9.25 6 2019-04-01 6343 9.18 7 2019-04-01 6286 9.11 8 2019-04-01 7541 8.94 9 2019-04-01 77 8.46 10 2019-05-01 5969 7.53 1 2019-05-01 6284 7.47 2 2019-05-01 12133 6.62 3 2019-05-01 10977 6.3 4 2019-05-01 77 6.23 5 2019-05-01 39 6.05 6 2019-05-01 10981 6.02 7 2019-05-01 19298 5.9 8 2019-05-01 64 5.89 9 2019-05-01 6286 5.82 10 2019-06-01 6284 6.94 1 2019-06-01 39 6.03 2 2019-06-01 77 5.53 3 2019-06-01 41548 5.03 4 2019-06-01 7535 4.67 5 2019-06-01 5969 4.63 6 2019-06-01 12025 4.61 7 2019-06-01 6324 4.59 8 2019-06-01 6206 4.55 9 2019-06-01 19250 4.5 10 2019-07-01 6284 7.19 1 2019-07-01 39 7.16 2 2019-07-01 77 6.52 3 2019-07-01 41548 5.91 4 2019-07-01 115 5.74 5 2019-07-01 7535 5.67 6 2019-07-01 6206 5.13 7 2019-07-01 5970 5.03 8 2019-07-01 6208 4.98 9 2019-07-01 5969 4.84 10 2019-07-01 12133 4.84 10 2019-08-01 6284 7.1 1 2019-08-01 41548 7.01 2 2019-08-01 39 6.76 3 2019-08-01 115 6.71 4 2019-08-01 77 6.48 5 2019-08-01 6206 6.19 6 2019-08-01 12133 5.86 7 2019-08-01 19250 5.68 8 2019-08-01 171 5.67 9 2019-08-01 151 5.62 10 2019-08-01 42203 5.62 10

2. For all of these top 10 interests - which interest appears the most often?

In [26]:
WITH CTE0 AS 
    (SELECT 
        CAST(CAST(month_year + '-01' AS nvarchar(10)) AS date) AS ConvertedDate,
        interest_id,
        AVG(composition) OVER (PARTITION BY month_year , interest_id ORDER BY composition DESC) AS AVG_COMPOSITION
    FROM filtered_data
    ),
CTE1 AS
    (
    SELECT 
        ConvertedDate,
        interest_id,
        AVG_COMPOSITION,
        DENSE_RANK() OVER (PARTITION BY ConvertedDate ORDER BY AVG_COMPOSITION DESC) AS AVG_COMPOSITION_RANKING
    FROM CTE0
    ),
CTE2 AS
    (
    SELECT 
        ConvertedDate,
        interest_id,
        AVG_COMPOSITION,
        AVG_COMPOSITION_RANKING
    FROM CTE1
    WHERE AVG_COMPOSITION_RANKING <= 10
    ),
CTE3 AS
    (
    SELECT 
        interest_id,
        COUNT(ConvertedDate) AS COUNT 
    FROM CTE2
    GROUP BY interest_id
    ),
CTE4 AS 
    (
    SELECT 
        interest_id,
        COUNT,
        DENSE_RANK() OVER (ORDER BY COUNT DESC) AS RANK
    FROM CTE3
    )

SELECT 
    interest_id 
FROM CTE4
WHERE RANK = 1

(3 rows affected)

Total execution time: 00:00:00.825

interest_id 12133 5969 6284

3. What is the average of the average composition for the top 10 interests for each month?

In [27]:
WITH CTE AS 
(
    SELECT
        CAST(CAST(month_year + '-01' AS nvarchar(10)) AS date) AS ConvertedDate,
        interest_id,
        AVG(composition) OVER (PARTITION BY month_year , interest_id ORDER BY month_year) AS AVG_COMPOSITION
    FROM fresh_segments.interest_metrics
    WHERE month_year != 'NO RECORD'
),CTE1 AS
(
    SELECT
        ConvertedDate,
        interest_id,
        AVG_COMPOSITION,
        DENSE_RANK() OVER (PARTITION BY ConvertedDate ORDER BY AVG_COMPOSITION DESC) AS AVG_COMPOSITION_RANK
    FROM CTE
),CTE2 AS
(
    SELECT 
        ConvertedDate,
        ROUND(AVG(AVG_COMPOSITION),2) AS [AVG OF AVG COMPOSITION FOR THE TOP 10 INTERESTS EACH MONTH]
    FROM CTE1
    WHERE AVG_COMPOSITION_RANK <= 10
    GROUP BY ConvertedDate
)

SELECT 
    ConvertedDate,
    [AVG OF AVG COMPOSITION FOR THE TOP 10 INTERESTS EACH MONTH]
FROM CTE2

(14 rows affected)

Total execution time: 00:00:05.260

ConvertedDate AVG OF AVG COMPOSITION FOR THE TOP 10 INTERESTS EACH MONTH 2018-07-01 15.06 2018-08-01 10.82 2018-09-01 12.2 2018-10-01 13.67 2018-11-01 12.26 2018-12-01 13.22 2019-01-01 12.11 2019-02-01 12.34 2019-03-01 10.89 2019-04-01 9.55 2019-05-01 6.38 2019-06-01 5.11 2019-07-01 5.73 2019-08-01 6.25

4. What is the 3 month rolling average of the max average composition value from September 2018 to August 2019 and include the previous top ranking interests in the same output shown below.

In [32]:
WITH CTE AS 
(
    SELECT 
        CAST(CAST(T1.month_year + '-01' AS nvarchar(10)) AS date) AS ConvertedDate,
        T2.interest_name,
        AVG(T1.composition) OVER (PARTITION BY T1.month_year , T2.INTEREST_NAME ORDER BY month_year) AS MAX_AVG_COMPOSITION
    FROM filtered_data T1 JOIN Fresh_Segments.interest_map T2
        ON T1.interest_id = T2.id
    WHERE T1.month_year != 'NO RECORD'
), CTE1 AS 
(
    SELECT 
        ConvertedDate,
        interest_name,
        MAX_AVG_COMPOSITION,
        DENSE_RANK() OVER (PARTITION BY ConvertedDate ORDER BY MAX_AVG_COMPOSITION DESC) AS AVG_COMPOSITION_RANK
    FROM CTE
),CTE2 AS 
(
    SELECT
        ConvertedDate,
        interest_name,
        MAX_AVG_COMPOSITION,
        AVG_COMPOSITION_RANK
    FROM CTE1
    WHERE AVG_COMPOSITION_RANK = 1
),CTE3 AS 
(
    SELECT 
        ConvertedDate,
        interest_name,
        MAX_AVG_COMPOSITION,
        AVG(MAX_AVG_COMPOSITION) OVER (ORDER BY ConvertedDate ROWS BETWEEN CURRENT ROW AND 2 FOLLOWING) AS [3 MONTHS MOVING AVERAGE]
    FROM CTE2
),CTE4 AS
(
    SELECT
        ConvertedDate,
        interest_name,
        MAX_AVG_COMPOSITION,
        [3 MONTHS MOVING AVERAGE],
        LAG(CONCAT(interest_name,': ',MAX_AVG_COMPOSITION),1,'NO INFO') OVER (ORDER BY ConvertedDate) AS [1 MONTH AGO],
        LAG(CONCAT(interest_name,': ',MAX_AVG_COMPOSITION),2,'NO INFO') OVER (ORDER BY ConvertedDate) AS [2 MONTHS AGO]
    FROM CTE3 
)

SELECT 
    ConvertedDate,
    interest_name,
    MAX_AVG_COMPOSITION,
    ROUND([3 MONTHS MOVING AVERAGE],2) AS [3 MONTHS MOVING AVERAGE],
    [1 MONTH AGO],
    [2 MONTHS AGO]
FROM CTE4
WHERE ConvertedDate BETWEEN '2018-09-01' AND '2019-08-01'

(12 rows affected)

Total execution time: 00:00:00.787

ConvertedDate interest_name MAX_AVG_COMPOSITION 3 MONTHS MOVING AVERAGE 1 MONTH AGO 2 MONTHS AGO 2018-09-01 Work Comes First Travelers 18.18 19.3 Gym Equipment Owners: 13.9 Gym Equipment Owners: 18.82 2018-10-01 Work Comes First Travelers 20.28 20.31 Work Comes First Travelers: 18.18 Gym Equipment Owners: 13.9 2018-11-01 Work Comes First Travelers 19.45 19.88 Work Comes First Travelers: 20.28 Work Comes First Travelers: 18.18 2018-12-01 Work Comes First Travelers 21.2 19.53 Work Comes First Travelers: 19.45 Work Comes First Travelers: 20.28 2019-01-01 Work Comes First Travelers 18.99 16.67 Work Comes First Travelers: 21.2 Work Comes First Travelers: 19.45 2019-02-01 Work Comes First Travelers 18.39 14.01 Work Comes First Travelers: 18.99 Work Comes First Travelers: 21.2 2019-03-01 Luxury Boutique Hotel Researchers 12.64 10.39 Work Comes First Travelers: 18.39 Work Comes First Travelers: 18.99 2019-04-01 Luxury Bedding Shoppers 11.01 8.49 Luxury Boutique Hotel Researchers: 12.64 Work Comes First Travelers: 18.39 2019-05-01 Luxury Bedding Shoppers 7.53 7.22 Luxury Bedding Shoppers: 11.01 Luxury Boutique Hotel Researchers: 12.64 2019-06-01 Gym Equipment Owners 6.94 7.08 Luxury Bedding Shoppers: 7.53 Luxury Bedding Shoppers: 11.01 2019-07-01 Gym Equipment Owners 7.19 7.14 Gym Equipment Owners: 6.94 Luxury Bedding Shoppers: 7.53 2019-08-01 Gym Equipment Owners 7.1 7.1 Gym Equipment Owners: 7.19 Gym Equipment Owners: 6.94